In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import os, random, zipfile, shutil
from pathlib import Path
from PIL import Image

# ==============================================================
# CONFIG
# ==============================================================
RAW_DRIVE      = '/content/drive/MyDrive/backgrounds_raw'      # folder with *.zip(s)
OUT_DRIVE      = '/content/drive/MyDrive/backgrounds_cropped' # final crops
ZIP_OUT        = '/content/drive/MyDrive/backgrounds_cropped_squares.zip'

FRAME_SIZE     = 1024
STEP_SIZE      = 512
PAD_COLOR      = (24, 24, 24)          # #181818
EXTS           = ('.jpg','.jpeg','.JPG','.JPEG','.webp','.WEBP')

os.makedirs(OUT_DRIVE, exist_ok=True)

# ==============================================================
# 1. FIND ALL ZIPs
# ==============================================================
zip_paths = [os.path.join(RAW_DRIVE, f) for f in os.listdir(RAW_DRIVE)
             if f.lower().endswith('.zip')]

if not zip_paths:
    print("No zip files found – nothing to do.")
else:
    print(f"Found {len(zip_paths)} zip file(s):")
    for p in zip_paths: print("  •", os.path.basename(p))

# ==============================================================
# 2. PROCESS EACH ZIP
# ==============================================================
with zipfile.ZipFile(ZIP_OUT, 'w') as master_zip:
    total_frames = 0

    for zip_idx, zip_path in enumerate(zip_paths, 1):
        # ---- extract to a unique temp folder ---------------------------------
        temp_dir = f'/content/raw_zip_{zip_idx}'
        os.makedirs(temp_dir, exist_ok=True)
        print(f"\n[{zip_idx}/{len(zip_paths)}] Extracting {os.path.basename(zip_path)} → {temp_dir}")
        with zipfile.ZipFile(zip_path, 'r') as z:
            z.extractall(temp_dir)

        # ---- walk through every image in this zip ----------------------------
        for root, _, files in os.walk(temp_dir):
            for filename in files:
                if not filename.lower().endswith(EXTS):
                    continue

                img_path = os.path.join(root, filename)
                try:
                    # ---- open & convert ---------------------------------------
                    with Image.open(img_path) as img:
                        img = img.convert('RGB')
                        w, h = img.size

                    # ---- 1. down-scale if any side > 1024 --------------------
                    if max(w, h) > FRAME_SIZE:
                        scale = FRAME_SIZE / max(w, h)
                        w, h = int(w*scale), int(h*scale)
                        img = img.resize((w, h), Image.LANCZOS)
                        # print(f"  ↓ {filename} → {w}×{h}")

                    # ---- 2. random-pad if any side < 1024 --------------------
                    if w < FRAME_SIZE or h < FRAME_SIZE:
                        target_w = max(w, FRAME_SIZE)
                        target_h = max(h, FRAME_SIZE)

                        pad_l = random.randint(0, target_w - w)
                        pad_r = target_w - w - pad_l
                        pad_t = random.randint(0, target_h - h)
                        pad_b = target_h - h - pad_t

                        padded = Image.new('RGB', (target_w, target_h), PAD_COLOR)
                        padded.paste(img, (pad_l, pad_t))
                        img = padded
                        w, h = target_w, target_h
                        # print(f"  ↔ {filename} → {w}×{h}")

                    # ---- 3. sliding-window crops -----------------------------
                    frame_cnt = 0
                    for y in range(0, max(h - FRAME_SIZE + 1, 1), STEP_SIZE):
                        for x in range(0, max(w - FRAME_SIZE + 1, 1), STEP_SIZE):
                            if x + FRAME_SIZE > w or y + FRAME_SIZE > h:
                                continue

                            crop = img.crop((x, y, x + FRAME_SIZE, y + FRAME_SIZE))

                            # use zip-index + original name to avoid collisions
                            crop_name = f"zip{zip_idx}_{Path(filename).stem}_f{frame_cnt}.jpg"
                            crop_path = os.path.join(OUT_DRIVE, crop_name)

                            crop.save(crop_path, "JPEG", quality=100)
                            master_zip.write(crop_path, arcname=crop_name)

                            frame_cnt += 1
                            total_frames += 1

                    if frame_cnt:
                        print(f"  → {filename} → {frame_cnt} crop(s)")

                except Exception as e:
                    print(f"  [ERROR] {filename}: {e}")

        # ---- clean this zip’s temp folder ---------------------------------
        print(f"Cleaning {temp_dir} …")
        shutil.rmtree(temp_dir, ignore_errors=True)

# ==============================================================
# DONE
# ==============================================================
print("\n=== ALL DONE ===")
print(f"Total crops created : {total_frames}")
print(f"Saved in            : {OUT_DRIVE}")
print(f"ZIP archive         : {ZIP_OUT}")

In [ ]:
# @title # Rounded Background Composer (1024x1024)

from google.colab import drive
drive.mount('/content/drive')

import os
from PIL import Image, ImageDraw
import zipfile
from pathlib import Path
import ipywidgets as widgets
from IPython.display import display

# === CONFIGURATION ===
input_folder = '/content/drive/MyDrive/backgrounds_cropped'      # from previous step
output_folder = '/content/drive/MyDrive/backgrounds_final_rounded'
zip_path = '/content/drive/MyDrive/backgrounds_final_rounded.zip'

os.makedirs(output_folder, exist_ok=True)

CANVAS_SIZE = 1024
BG_COLOR = (24, 24, 24)  # #181818

# === Interactive Sliders ===
print("Adjust settings below, then run the next cell:")

border_slider = widgets.IntSlider(
    value=10, min=0, max=100, step=1,
    description='Border (px):',
    style={'description_width': 'initial'}
)

radius_slider = widgets.IntSlider(
    value=30, min=0, max=200, step=1,
    description='Corner Radius (px):',
    style={'description_width': 'initial'}
)

display(border_slider, radius_slider)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Adjust settings below, then run the next cell:


IntSlider(value=10, description='Border (px):', style=SliderStyle(description_width='initial'))

IntSlider(value=30, description='Corner Radius (px):', max=200, style=SliderStyle(description_width='initial')…

In [ ]:
# @title Run Processing (after setting sliders)

border_size = border_slider.value
corner_radius = radius_slider.value

print(f"Using: Border = {border_size}px | Corner Radius = {corner_radius}px")

# Helper: Create rounded mask
def create_rounded_mask(size, radius):
    mask = Image.new('L', size, 0)
    draw = ImageDraw.Draw(mask)
    draw.rounded_rectangle([(0,0), size], radius, fill=255)
    return mask

# Supported extensions
extensions = ('.jpg', '.jpeg', '.png', '.webp')

with zipfile.ZipFile(zip_path, 'w', zipfile.ZIP_DEFLATED) as zipf:
    processed = 0

    for filename in os.listdir(input_folder):
        if filename.lower().endswith(extensions):
            img_path = os.path.join(input_folder, filename)

            try:
                with Image.open(img_path).convert("RGB") as img:
                    # --- Create canvas ---
                    canvas = Image.new("RGB", (CANVAS_SIZE, CANVAS_SIZE), BG_COLOR)

                    # --- Inner area size ---
                    inner_size = CANVAS_SIZE - 2 * border_size
                    if inner_size <= 0:
                        print(f"Skip {filename}: border too large")
                        continue

                    # --- Resize image to fit inner area ---
                    img_resized = img.resize((inner_size, inner_size), Image.LANCZOS)

                    # --- Apply rounded corners ---
                    if corner_radius > 0:
                        radius = min(corner_radius, inner_size // 2)
                        mask = create_rounded_mask((inner_size, inner_size), radius)
                        rounded_img = Image.new("RGBA", (inner_size, inner_size), (0,0,0,0))
                        rounded_img.paste(img_resized, (0,0))
                        rounded_img.putalpha(mask)
                        # Convert back to RGB by compositing on gray
                        final_inner = Image.new("RGB", (inner_size, inner_size), BG_COLOR)
                        final_inner.paste(rounded_img, (0,0), rounded_img)
                    else:
                        final_inner = img_resized

                    # --- Paste in center ---
                    paste_x = border_size
                    paste_y = border_size
                    canvas.paste(final_inner, (paste_x, paste_y))

                    # --- Save ---
                    output_name = f"{Path(filename).stem}_1024_border{border_size}_r{corner_radius}.png"
                    output_path = os.path.join(output_folder, output_name)
                    canvas.save(output_path, "PNG", optimize=True)

                    # --- Add to ZIP ---
                    zipf.write(output_path, arcname=output_name)

                    print(f"Created: {output_name}")
                    processed += 1

            except Exception as e:
                print(f"Error with {filename}: {e}")

print(f"\nFinished! {processed} images processed.")
print(f"Folder: {output_folder}")
print(f"ZIP: {zip_path}")

##Randomly add manga panels to the newly created backgrounds using rembg

In [ ]:
# @title 1. Setup & Unzip Manga Images
# (unchanged – only the config variables are used later)

!pip install rembg pillow numpy onnxruntime -q

from google.colab import drive
drive.mount('/content/drive')

import os, random, zipfile, shutil
from pathlib import Path
from PIL import Image
import numpy as np
from rembg import remove

# === CONFIG ===
MANGA_ZIP = '/content/drive/MyDrive/backgrounds_cropped_squares.zip' #@param {type:'string'}
BG_FOLDER = '/content/drive/MyDrive/backgrounds_final_rounded'  # From previous step
OUTPUT_FOLDER = '/content/manga_on_bg'

# Generate a random 5-digit number
random_suffix = random.randint(10000, 99999)  # 5 digits
ZIP_OUTPUT = f'/content/drive/MyDrive/manga_on_backgrounds_{random_suffix}.zip'

# Unzip manga
!unzip -q "$MANGA_ZIP" -d /content/

# Clean & recreate output
if os.path.exists(OUTPUT_FOLDER):
    shutil.rmtree(OUTPUT_FOLDER)
os.makedirs(OUTPUT_FOLDER, exist_ok=True)

print("Manga images extracted to /content/")
print(f"Backgrounds folder: {BG_FOLDER}")
print(f"Output will be saved to: {ZIP_OUTPUT}")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.1/44.1 kB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.4/17.4 MB 26.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.7/54.7 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 3.1 MB/s eta 0:00:00
Mounted at /content/drive
Manga images extracted to /content/
Backgrounds folder: /content/drive/MyDrive/backgrounds_final_rounded
Output will be saved to: /content/drive/MyDrive/manga_on_backgrounds_34664.zip


In [ ]:
# @title 2. Process: Remove BG → Place on **5 different** Random Backgrounds (with Random Flip)

import os, random, zipfile
import numpy as np
from PIL import Image
from rembg import remove

# ------------------------------------------------------------------
# 1. Load *all* background images
# ------------------------------------------------------------------
all_bgs = [
    os.path.join(BG_FOLDER, f)
    for f in os.listdir(BG_FOLDER)
    if f.lower().endswith(('.png', '.jpg', '.jpeg'))
]
print(f"Found {len(all_bgs)} background images")

# ------------------------------------------------------------------
# 2. Find all manga panels (FIXED: no f[0].isdigit() restriction)
# ------------------------------------------------------------------
manga_files = sorted([
    f for f in os.listdir('/content')
    if f.lower().endswith(('.jpg', '.jpeg', '.png'))
    and not f.startswith('.')           # ignore hidden files
    and os.path.isfile(os.path.join('/content', f))
])
print(f"Processing {len(manga_files)} manga images: {manga_files[:5]}..." if manga_files else "No manga images found!")

# ------------------------------------------------------------------
# 3. Output ZIP
# ------------------------------------------------------------------
os.makedirs(OUTPUT_FOLDER, exist_ok=True)

with zipfile.ZipFile(ZIP_OUTPUT, 'w', zipfile.ZIP_DEFLATED) as zipf:
    for idx, manga_name in enumerate(manga_files, 1):
        manga_path = os.path.join('/content', manga_name)

        try:
            # ---- Open manga & remove background (once) ----
            with Image.open(manga_path).convert("RGBA") as manga_img:
                manga_np = np.array(manga_img)
                output = remove(manga_np)
                manga_nobg = Image.fromarray(output).convert("RGBA")

            # ---- Pick 5 different random backgrounds ----
            chosen_bgs = random.sample(all_bgs, k=min(5, len(all_bgs)))

            for bg_idx, bg_path in enumerate(chosen_bgs, 1):
                with Image.open(bg_path).convert("RGBA") as bg_img:
                    bg = bg_img.copy()

                # ---- Resize manga to background height ----
                target_h = bg.height
                ratio = target_h / manga_nobg.height
                new_w = int(manga_nobg.width * ratio)
                manga_resized = manga_nobg.resize((new_w, target_h), Image.LANCZOS)

                # ---- Generate LEFT and RIGHT versions ----
                for place_left in (True, False):
                    paste_x = 0 if place_left else bg.width - manga_resized.width
                    align_desc = "left" if place_left else "right"

                    # ---- Random flip (50% chance) ----
                    manga_to_paste = manga_resized.copy()
                    if random.random() < 0.5:
                        manga_to_paste = manga_to_paste.transpose(Image.FLIP_LEFT_RIGHT)
                        flip_desc = "flip"
                    else:
                        flip_desc = "noflip"

                    # Paste
                    result_bg = bg.copy()
                    result_bg.paste(manga_to_paste, (paste_x, 0), manga_to_paste)

                    # ---- Save & zip ----
                    result_name = f"{idx:03d}_bg{bg_idx:02d}_{align_desc}_{flip_desc}.png"
                    result_path = os.path.join(OUTPUT_FOLDER, result_name)
                    result_bg.convert("RGB").save(result_path, "PNG")
                    zipf.write(result_path, result_name)

                    print(f"{idx}/{len(manga_files)} → {result_name}")

        except Exception as e:
            print(f"Error with {manga_name}: {e}")

print(f"\nAll done! ZIP saved to:\n{ZIP_OUTPUT}")
print(f"Individual files in:\n{OUTPUT_FOLDER}")

Found 634 background images
Processing 634 manga images: ['zip1_008e679eb0a5080a373abbefa0ef7570_f0.jpg', 'zip1_06b225f210d032734c22758475a462bc_f0.jpg', 'zip1_12717f1849c5791b41958543e394ed24_f0.jpg', 'zip1_14c7e9cf5d9251efb5c70c70bda8ea5a_f0.jpg', 'zip1_1e44ed908d7585349f4072a6c446d8f9_f0.jpg']...


100%|███████████████████████████████████████| 176M/176M [00:00<00:00, 92.1GB/s]


1/634 → 001_bg01_left_flip.png
1/634 → 001_bg01_right_flip.png
1/634 → 001_bg02_left_noflip.png
1/634 → 001_bg02_right_noflip.png
1/634 → 001_bg03_left_noflip.png
1/634 → 001_bg03_right_flip.png
1/634 → 001_bg04_left_noflip.png
1/634 → 001_bg04_right_flip.png
1/634 → 001_bg05_left_noflip.png
1/634 → 001_bg05_right_noflip.png
2/634 → 002_bg01_left_flip.png
2/634 → 002_bg01_right_noflip.png
2/634 → 002_bg02_left_flip.png
2/634 → 002_bg02_right_flip.png
2/634 → 002_bg03_left_noflip.png
2/634 → 002_bg03_right_flip.png
2/634 → 002_bg04_left_flip.png
2/634 → 002_bg04_right_flip.png
2/634 → 002_bg05_left_flip.png
2/634 → 002_bg05_right_flip.png
3/634 → 003_bg01_left_flip.png
3/634 → 003_bg01_right_flip.png
3/634 → 003_bg02_left_flip.png
3/634 → 003_bg02_right_flip.png
3/634 → 003_bg03_left_flip.png
3/634 → 003_bg03_right_flip.png
3/634 → 003_bg04_left_flip.png
3/634 → 003_bg04_right_noflip.png
3/634 → 003_bg05_left_flip.png
3/634 → 003_bg05_right_flip.png
4/634 → 004_bg01_left_flip.png
4/634 